<a href="https://colab.research.google.com/github/plaban1981/Hugging_Face_transformers_topics/blob/main/Copy_of_MusicGen_Demo.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!python -m pip install -U git+https://github.com/facebookresearch/audiocraft#egg=audiocraft
# !python3 -m pip install -U audiocraft

We provide a simple API and 4 pre-trained models. The pre trained models are:

* small: 300M model, text to music only - 🤗 Hub
* medium: 1.5B model, text to music only - 🤗 Hub
* melody: 1.5B model, text to music and text+melody to music - 🤗 Hub
* large: 3.3B model, text to music only - 🤗 Hub

We observe the best trade-off between quality and compute with the medium or melody model.

In order to use MusicGen locally you must have a GPU. We recommend 16GB of memory, but smaller GPUs will be able to generate short sequences, or longer sequences with the small model.

#### Note: Please make sure to have ffmpeg installed when using newer version of torchaudio. You can install it with:

In [58]:
import torch

In [1]:
! pip install -U git+https://github.com/facebookresearch/audiocraft#egg=audiocraft

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Cloning https://github.com/facebookresearch/audiocraft to /tmp/pip-install-f40ff4ph/audiocraft_94fd2a4fdb224d6296a7690bcb899d2c
  Running command git clone --filter=blob:none --quiet https://github.com/facebookresearch/audiocraft /tmp/pip-install-f40ff4ph/audiocraft_94fd2a4fdb224d6296a7690bcb899d2c
  Resolved https://github.com/facebookresearch/audiocraft to commit 6d70065e31c2fb422a76237e03740dd3b627de8d
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 31.0/31.0 MB 56.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.2/42.2 kB 5.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 72.4/72.4 kB 9.6 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 154.5/154.5 kB 20.3 MB/s eta 

In [59]:
print(torch.__version__)

2.0.1+cu118


In [37]:
from audiocraft.models import musicgen
from audiocraft.data.audio_utils import convert_audio
from audiocraft.data.audio import audio_write
from audiocraft.models import MusicGen
from audiocraft.utils.notebook import display_audio
import torch
from io import BytesIO

In [38]:
model = musicgen.MusicGen.get_pretrained('medium', device='cuda')
model.set_generation_params(use_sampling=True,
                            top_k=250,
                            top_p=0,
                            temperature=1.0,
                            cfg_coef=3.0,
                            duration=30)

In [39]:
res = model.generate(['An 80s driving pop song with heavy drums and synth pads in the background'],
    progress=True)
display_audio(res, 32000)

In [54]:
%%writefile input.txt
a light and cheerly EDM track, with syncopated drums, aery pads, and strong emotions bpm: 130

Writing input.txt


In [40]:
output = res.detach().cpu().float()[0]
with open("music_30.wav","wb") as file:
  audio_write(
            file.name, output, model.sample_rate, strategy="loudness",
            loudness_headroom_db=16, loudness_compressor=True, add_suffix=False)
  #music_video = make_waveform(file.name)

In [53]:
import os
os.remove("/content/music.wav")

In [41]:
from IPython.display import Audio
Audio('/content/music_30.wav')

In [45]:
import numpy as np

In [44]:
def pad_buffer(audio):
    # Pad buffer to multiple of 2 bytes
    buffer_size = len(audio)
    element_size = np.dtype(np.int16).itemsize
    if buffer_size % element_size != 0:
        audio = audio + b'\0' * (element_size - (buffer_size % element_size))
    return audio

In [42]:
type(output)

torch.Tensor

In [47]:
import pickle
# Step 1: Convert tensor to NumPy array
numpy_array = output.numpy()

In [49]:
# Step 2: Serialize the NumPy array into a byte string
serialized_bytes = pickle.dumps(numpy_array)

In [50]:
# Step 3: Create a BytesIO object and write the serialized byte string to it
bytes_io = BytesIO()
bytes_io.write(serialized_bytes)

3840164

In [43]:
from io import BytesIO
audio = BytesIO('/content/music_30.wav')

TypeError: ignored

## Inference Script

In [56]:
from audiocraft.models import musicgen
from audiocraft.data.audio_utils import convert_audio
from audiocraft.data.audio import audio_write
from audiocraft.models import MusicGen
from audiocraft.utils.notebook import display_audio
import torch
from io import BytesIO
import json
import os
from uuid import uuid4

#
def preprocess_function(request_data, content_type=None):
    #'''
    with open(request_data,"r",encoding='utf-8') as f:
        data = f.read()
    print(data)
    #'''
    #data = request_data["input_text"]
    return data

#
#
def predict_function(context, model):
  model.set_generation_params(use_sampling=True,
                            top_k=250,
                            top_p=0,
                            temperature=1.0,
                            cfg_coef=3.0,
                            duration=30)
  res = model.generate([context],progress=True)
  return res
#
def model_load_function(model_path):
    model = musicgen.MusicGen.get_pretrained('medium', device='cuda')
    return model
#
def postprocess_function(predictions, content_type=None):
  output = predictions.detach().cpu().float()[0]
  uid = uuid4().hex
  file_name = f"Audio_{uid}.wav"
  with open(file_name,"wb") as file:
    audio_write(
            file.name, output, model.sample_rate, strategy="loudness",
            loudness_headroom_db=16, loudness_compressor=True, add_suffix=False)
  with open(file_name,"rb") as fh:
    buf = BytesIO(fh.read())
  audio = buf
  return {"audio":{"data":audio,"ext":"wav"}}


In [57]:
if __name__ == '__main__':
    txt_path = "/content/input.txt"
    data = preprocess_function(txt_path)
    model_path = "./model_files"
    path = model_load_function(model_path)
    predictions = predict_function(data,path)
    out = postprocess_function(predictions)
    print(out)

a light and cheerly EDM track, with syncopated drums, aery pads, and strong emotions bpm: 130

{'audio': {'data': <_io.BytesIO object at 0x7f6cb8d36e80>, 'ext': 'wav'}}


In [3]:
res = model.generate([
    'crazy EDM, heavy bang',
    'classic reggae track with an electronic guitar solo',
    'lofi slow bpm electro chill with organic samples',
    'rock with saturated guitars, a heavy bass line and crazy drum break and fills.',
    'earthy tones, environmentally conscious, ukulele-infused, harmonic, breezy, easygoing, organic instrumentation, gentle grooves',
],
    progress=True)
display_audio(res, 32000)

In [25]:
output = res.detach().cpu().float()[0]
with NamedTemporaryFile("wb", suffix=".wav", delete=False) as file:
  audio_write(
            file.name, output, model.sample_rate, strategy="loudness",
            loudness_headroom_db=16, loudness_compressor=True, add_suffix=False)
  waveform_video = make_waveform(file.name)

CLIPPING /tmp/tmpu4_9h60i.wav happening with proba (a bit of clipping is okay): 2.7343750844011083e-05 maximum scale:  1.1327719688415527


Make a video took 1.2982962131500244


In [26]:
waveform_video

'/tmp/tmp4jbk6qe7.mp4'

In [33]:
music_video

'/tmp/tmpjf085fn0.mp4'

In [36]:
from IPython.display import Audio
Audio('/content/music.wav')

See our repo https://github.com/facebookresearch/audiocraft for more details on how to use this model!

See also [MusicGen Gradio Demo](https://colab.research.google.com/drive/1-Xe9NCdIs2sCUbiSmwHXozK6AAhMm7_i?usp=sharing) for a Colab using the Gradio app instead!


In [23]:
from tempfile import NamedTemporaryFile
import time
import warnings
import torch
import gradio as gr
from audiocraft.data.audio_utils import convert_audio
from audiocraft.data.audio import audio_write
from audiocraft.models import MusicGen

In [20]:
MODEL = None
#IS_SHARED_SPACE = "musicgen/MusicGen" in os.environ.get('SPACE_ID', '')


def load_model(version):
    print("Loading model", version)
    return MusicGen.get_pretrained(version)


def predict(model, text, melody, duration):
    global MODEL
    #topk = int(topk)
    if MODEL is None or MODEL.name != model:
        MODEL = load_model(model)

    if duration > MODEL.lm.cfg.dataset.segment_duration:
        raise Exception("MusicGen currently supports durations of up to 30 seconds!")
    MODEL.set_generation_params(
        use_sampling=True,
        top_k=250,
        top_p=0,
        temperature=1.0,
        cfg_coef=3.0,
        duration=duration,
    )

    if melody:
        sr, melody = melody[0], torch.from_numpy(melody[1]).to(MODEL.device).float().t().unsqueeze(0)
        print(melody.shape)
        if melody.dim() == 2:
            melody = melody[None]
        melody = melody[..., :int(sr * MODEL.lm.cfg.dataset.segment_duration)]
        output = MODEL.generate_with_chroma(
            descriptions=[text],
            melody_wavs=melody,
            melody_sample_rate=sr,
            progress=False
        )
    else:
        output = MODEL.generate(descriptions=[text], progress=False)

    output = output.detach().cpu().float()[0]
    with NamedTemporaryFile("wb", suffix=".wav", delete=False) as file:
        audio_write(
            file.name, output, MODEL.sample_rate, strategy="loudness",
            loudness_headroom_db=16, loudness_compressor=True, add_suffix=False)
        waveform_video = gr.make_waveform(file.name)
    return waveform_video


In [34]:
inputs = [
                    "An 80s driving pop song with heavy drums and synth pads in the background",
                    "./assets/bach.mp3",
                    "melody",30
                ]
predict(model="melody",text="An 80s driving pop song with heavy drums and synth pads in the background",melody="",duration=30)


CLIPPING /tmp/tmp7v74p__u.wav happening with proba (a bit of clipping is okay): 3.645833203336224e-05 maximum scale:  1.324372410774231
/usr/local/lib/python3.10/dist-packages/matplotlib/axes/_axes.py:2229: RuntimeWarning: overflow encountered in short_scalars
  dx = [convert(x0 + ddx) - x for ddx in dx]
/usr/local/lib/python3.10/dist-packages/matplotlib/patches.py:739: RuntimeWarning: overflow encountered in short_scalars
  y1 = self.convert_yunits(self._y0 + self._height)


'/tmp/tmpm5ovgvty.mp4'

In [35]:
from IPython.display import Audio
Audio('/tmp/tmpm5ovgvty.mp4')